# Figure3 - scRNA-seq without known cell-types or marker genes


Last updated: 1/30/2023

Author: Yang-Joon Kim

In [32]:
import scanpy as sc
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import networkx as nx
from networkx.algorithms import dag_longest_path
from scipy.cluster.hierarchy import linkage, dendrogram
from sklearn.preprocessing import normalize

In [2]:
# load the dataset
adata = sc.read('/mnt/ibm_lg/alejandro/danio-atlas/zebrahub/final_objects/v4/zf_atlas_24hpf_v4_release.h5ad')

# Sankey diagram for leiden resolution

- We want to find a leiden clustering resolution that is a good starting point for DGE.
- For this, we will try several resolutions of leiden clustering, then see if there's a pattern in terms of resolution that we'd like to start annotation from.



In [14]:
adata

AnnData object with n_obs × n_vars = 12914 × 32060
    obs: 'n_genes', 'n_counts', 'fish', 'timepoint_cluster', 'n_genes_by_counts', 'total_counts', 'total_counts_mt', 'pct_counts_mt', 'total_counts_nc', 'pct_counts_nc', 'zebrafish_anatomy_ontology_class', 'zebrafish_anatomy_ontology_id', 'developmental_stage', 'timepoint'
    var: 'gene_ids', 'feature_types', 'genome', 'mt', 'nc', 'n_cells_by_counts', 'mean_counts', 'pct_dropout_by_counts', 'total_counts', 'n_cells'
    uns: 'timepoint_colors', 'zebrafish_anatomy_ontology_class_colors', 'pca', 'neighbors'
    obsm: 'X_umap', 'X_pca'
    varm: 'PCs'
    layers: 'counts'
    obsp: 'distances', 'connectivities'

In [12]:
# re-compute PCA and neighbors
sc.tl.pca(adata, svd_solver='arpack')
sc.pp.neighbors(adata, n_neighbors=10, n_pcs=40)


2023-01-30 22:11:23.346506: I tensorflow/core/util/util.cc:169] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.


In [15]:
# compute leiden clustering and save those in adata.uns with specified keys
sc.tl.leiden(adata, resolution=0.05, key_added="leiden_0.05")
sc.tl.leiden(adata, resolution=0.1, key_added="leiden_0.1")
sc.tl.leiden(adata, resolution=0.2, key_added="leiden_0.2")
sc.tl.leiden(adata, resolution=0.3, key_added="leiden_0.3")
sc.tl.leiden(adata, resolution=0.4, key_added="leiden_0.4")
sc.tl.leiden(adata, resolution=0.5, key_added="leiden_0.5")
sc.tl.leiden(adata, resolution=0.75, key_added="leiden_0.75")
sc.tl.leiden(adata, resolution=1.0, key_added="leiden_1.0")

In [19]:
adata.obs

n_genes  n_counts   fish timepoint_cluster  \
cell_id                                                                
TDR43_ACCCAAAAGCACGATG-1     2813   18114.0  TDR43                 4   
TDR46_GTTCATTGTTTGAAAG-1     3820   20816.0  TDR46                28   
TDR43_TCCCATGAGCTAAATG-1     3997   24222.0  TDR43                14   
TDR43_ACTACGACACGACGTC-1     6678   59204.0  TDR43                10   
TDR46_AACGTCAAGCAACTTC-1     3563   19216.0  TDR46                14   
...                           ...       ...    ...               ...   
TDR44_AGAGCAGTCGCTCCTA-1     4415   32708.0  TDR44                 1   
TDR46_AACAACCTCAACTGGT-1     3801   18535.0  TDR46                19   
TDR43_CTGCATCTCAACTCTT-1     4011   24127.0  TDR43                11   
TDR45_CCGGTAGTCATTTGCT-1     3662   20837.0  TDR45                18   
TDR43_TCAGTTTTCTCGCTTG-1     4787   32267.0  TDR43                 7   

                          n_genes_by_counts  total_counts  total_counts_mt  \
cell_id                                                                      
TDR43_ACCCAAAAGCACGATG-1               2813       18114.0            280.0   
TDR46_GTTCATTGTTTGAAAG-1               3820       20816.0            481.0   
TDR43_TCCCATGAGCTAAATG-1               3997       24222.0            321.0   
TDR43_ACTACGACACGACGTC-1               6678       59204.0           1018.0   
TDR46_AACGTCAAGCAACTTC-1               3563       19216.0            228.0   
...                                     ...           ...              ...   
TDR44_AGAGCAGTCGCTCCTA-1               4415       32708.0            495.0   
TDR46_AACAACCTCAACTGGT-1               3801       18535.0            402.0   
TDR43_CTGCATCTCAACTCTT-1               4011       24127.0            647.0   
TDR45_CCGGTAGTCATTTGCT-1               3662       20837.0            122.0   
TDR43_TCAGTTTTCTCGCTTG-1               4787       32267.0            585.0   

                          pct_counts_mt  total_counts_nc  pct_counts_nc  ...  \
cell_id                                                                  ...   
TDR43_ACCCAAAAGCACGATG-1       1.545766            261.0       1.440874  ...   
TDR46_GTTCATTGTTTGAAAG-1       2.310723            261.0       1.253843  ...   
TDR43_TCCCATGAGCTAAATG-1       1.325241            243.0       1.003220  ...   
TDR43_ACTACGACACGACGTC-1       1.719478            516.0       0.871563  ...   
TDR46_AACGTCAAGCAACTTC-1       1.186511            223.0       1.160491  ...   
...                                 ...              ...            ...  ...   
TDR44_AGAGCAGTCGCTCCTA-1       1.513391            413.0       1.262688  ...   
TDR46_AACAACCTCAACTGGT-1       2.168870            261.0       1.408147  ...   
TDR43_CTGCATCTCAACTCTT-1       2.681643            585.0       2.424670  ...   
TDR45_CCGGTAGTCATTTGCT-1       0.585497            270.0       1.295772  ...   
TDR43_TCAGTTTTCTCGCTTG-1       1.812998            255.0       0.790281  ...   

                         developmental_stage timepoint leiden_0.05 leiden_0.1  \
cell_id                                                                         
TDR43_ACCCAAAAGCACGATG-1          30 somites     24hpf           0          0   
TDR46_GTTCATTGTTTGAAAG-1          30 somites     24hpf           0          6   
TDR43_TCCCATGAGCTAAATG-1          30 somites     24hpf           0          1   
TDR43_ACTACGACACGACGTC-1          30 somites     24hpf           3          3   
TDR46_AACGTCAAGCAACTTC-1          30 somites     24hpf           0          1   
...                                      ...       ...         ...        ...   
TDR44_AGAGCAGTCGCTCCTA-1          30 somites     24hpf           0          0   
TDR46_AACAACCTCAACTGGT-1          30 somites     24hpf           0          1   
TDR43_CTGCATCTCAACTCTT-1          30 somites     24hpf           0          0   
TDR45_CCGGTAGTCATTTGCT-1          30 somites     24hpf           3          3   
TDR43_TCAGTTTTCTCGCTTG-1          30 somites     24hpf       

In [26]:
from pyvis.network import Network

# Define the range of resolutions to compute Leiden clustering
resolutions = np.arange(0.1, 1.1, 0.1)

# Initialize a dictionary to store the results of Leiden clustering for each resolution
leiden_results = {}

# Loop over the range of resolutions
for resolution in resolutions:
    sc.tl.leiden(adata, resolution=resolution, key_added='leiden_clusters_res_{}'.format(resolution))
    leiden_results[resolution] = adata.obs['leiden_clusters_res_{}'.format(resolution)].tolist()

# Convert the results of Leiden clustering to a DataFrame
leiden_df = pd.DataFrame(leiden_results)
leiden_df

# # Loop over the range of resolutions to generate a sankey diagram for each resolution
# for resolution in resolutions:
#     # Compute the pairwise co-occurrence matrix
#     co_occurrence_matrix = np.zeros((leiden_df['leiden_clusters_res_{}'.format(resolution)].nunique(), 
#                                      leiden_df['leiden_clusters_res_{}'.format(resolution)].nunique()))
#     for i, cluster1 in enumerate(leiden_df['leiden_clusters_res_{}'.format(resolution)].unique()):
#         for j, cluster2 in enumerate(leiden_df['leiden_clusters_res_{}'.format(resolution)].unique()):
#             co_occurrence_matrix[i, j] = np.sum((leiden_df['leiden_clusters_res_{}'.format(resolution)] == cluster1) & 
#                                                 (leiden_df['leiden_clusters_res_{}'.format(resolution)] == cluster2))
#     co_occurrence_matrix = normalize(co_occurrence_matrix, axis=1, norm='l1')
    
#     # Create the directed graph
#     graph = nx.DiGraph(co_occurrence_matrix)
    
#     # Compute the longest path in the directed acyclic graph
#     node_list = dag_longest_path(graph)
    

#     # Create a Network object with the longest path matrix
#     net = Network(notebook=True, height="800px", width="100%")
#     net.add_nodes(node_list)
#     for i, node1 in enumerate(node_list):
#         for j, node2 in enumerate(node_list):
#             if path_matrix[i, j] > 0:
#                 net.add_edge(node1, node2, value=path_matrix[i, j])

#     # Set the node and edge colors
#     net.toggle_stretch(True)
#     net.barnes_hut()

# # Generate the sankey diagram
# net.show("sankey_diagram_res_{}.html".format(resolution))
    
#     # Compute the normalized co-occurrence matrix for the longest path
#     path_matrix = np.zeros((len(node_list), len(node_list)))
#     for i, node1 in enumerate(node_list):
#         for j, node2 in enumerate(node_list):
#             path_matrix[i, j]

0.1 0.2 0.3 0.4 0.5 0.6 0.7 0.8 0.9 1.0
0       0   1   1   8   1   3   1  24  25  17
1       6   7   7   8  12  11  13  26  27  27
2       1   2   2   2   6   5   5   5   5   5
3       3   4   4   3   8   8   7   7   8   7
4       1   2   2   2   6   5   5   5   5   5
...    ..  ..  ..  ..  ..  ..  ..  ..  ..  ..
12909   0   7   7   8  12  11  13  12  11  15
12910   1   2   2   2  11  12  11  13  12  12
12911   0   1   1   1   1   3   1   3   1   3
12912   3   4   4   3   8   8   7   7   8   7
12913   1   2   2   2   4  14  15  15  15  14

[12914 rows x 10 columns]

In [28]:
# Build a directed graph where each node represents a cluster
# and each edge represents the flow of cells from one cluster to another
# G = nx.DiGraph()
# for i in range(leiden_df.shape[0]):
#     for j in range(leiden_df.shape[1] - 1):
#         G.add_edge(leiden_df.iloc[i, j], leiden_df.iloc[i, j + 1], weight=1)

# # Plot the network diagram using matplotlib
# pos = nx.kamada_kawai_layout(G)
# nx.draw(G, pos, node_size=0, alpha=0.5, arrows=False, with_labels=False)
# edge_labels = nx.get_edge_attributes(G, 'weight')
# nx.draw_networkx_edge_labels(G, pos, edge_labels=edge_labels)
# plt.show()
import plotly.express as px

# Create a source-target dataframe
df_sankey = pd.DataFrame({'source': [], 'target': [], 'value': []})
for i in range(leiden_df.shape[0]):
    for j in range(leiden_df.shape[1] - 1):
        df_sankey = pd.concat([df_sankey, pd.DataFrame({'source': [leiden_df.iloc[i, j]], 
                                                        'target': [leiden_df.iloc[i, j + 1]], 
                                                        'value': [1]})], ignore_index=True)

# Plot the sankey diagram using plotly
fig = px.sankey(df_sankey, source='source', target='target', value='value')
fig.show()

AttributeError: module 'plotly.express' has no attribute 'sankey'

In [34]:
df_sankey

source target  value
0           0      1    1.0
1           1      1    1.0
2           1      8    1.0
3           8      1    1.0
4           1      3    1.0
...       ...    ...    ...
116221      4     14    1.0
116222     14     15    1.0
116223     15     15    1.0
116224     15     15    1.0
116225     15     14    1.0

[116226 rows x 3 columns]

In [33]:
import plotly.graph_objs as go
# Plot the sankey diagram using plotly
fig = go.Figure(data=[go.Sankey(node=dict(label=df_sankey['source'].unique()),
                     link=dict(source=df_sankey['source'], target=df_sankey['target'], value=df_sankey['value']))])

fig.show()

In [31]:
import networkx as nx
import matplotlib.pyplot as plt

# Build a directed graph where each node represents a cluster
# and each edge represents the flow of cells from one cluster to another
G = nx.DiGraph()
for i in range(df.shape[0]):
    for j in range(df.shape[1] - 1):
        G.add_edge(df.iloc[i, j], df.iloc[i, j + 1], weight=1)

# Plot the sankey diagram using matplotlib
pos = nx.kamada_kawai_layout(G)
nx.draw(G, pos, node_size=0, alpha=0.5, arrows=False, with_labels=False)
edge_labels = nx.get_edge_attributes(G, 'weight')
nx.draw_networkx_edge_labels(G, pos, edge_labels=edge_labels)
plt.show()

NameError: name 'df' is not defined